In [ ]:
!wget https://noble.gs.washington.edu/~ranz0/external/Polarbear/run_multivi/data_multivi.h5ad
!pip install scvi-tools

In [1]:
import scvi
import anndata
import scanpy
import scipy
import numpy as np
import pandas as pd

scvi.settings.seed = 420

Global seed set to 0
/usr/local/lib/python3.7/dist-packages/numba/np/ufunc/parallel.py:363: NumbaWarning: The TBB threading layer requires TBB version 2019.5 or later i.e., TBB_INTERFACE_VERSION >= 11005. Found TBB_INTERFACE_VERSION = 9107. The TBB threading layer is disabled.
  warnings.warn(problem)
Global seed set to 420


In [2]:
adata_mvi = scvi.data.read_h5ad('data_multivi.h5ad')
#adata_mvi = adata_mvi[1:10000,:] # took a subset of cells, also ran out of memory
#adata_mvi = adata_mvi.copy()

In [3]:
# optional, but will make it run much faster
print(adata_mvi.shape)
scanpy.pp.filter_genes(adata_mvi, min_cells=int(adata_mvi.shape[0] * 0.01))
scanpy.pp.filter_cells(adata_mvi, min_genes=int(adata_mvi.shape[1] * 0.01))
print(adata_mvi.shape)

(341547, 237797)
(280620, 27670)


In [4]:
scvi.model.MULTIVI.setup_anndata(adata_mvi, batch_key='modality')
mvi = scvi.model.MULTIVI(
    adata_mvi,
    n_genes=(adata_mvi.var['modality']=='Gene Expression').sum(),
    n_regions=(adata_mvi.var['modality']=='Peaks').sum(),
)

INFO     Using batches from adata.obs["modality"]                                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.X                                                             
INFO     Successfully registered anndata object containing 280620 cells, 27670 vars, 3       
         batches, 1 labels, and 0 proteins. Also registered 0 extra categorical covariates   
         and 0 extra continuous covariates.                                                  
INFO     Please do not further modify adata until model is trained.                          


In [ ]:
#mvi.train(batch_size=4)
# mvi.train(batch_size=128)
mvi.train()

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Epoch 3/500:   0%|          | 2/500 [06:11<25:14:16, 182.44s/it, loss=1.93e+03, v_num=1]

In [ ]:
mvi.save("trained_multivi")